# Business Data Challenge - Team 1

In [ ]:
import pandas as pd
import numpy as np

Configuration de l'accès aux données

In [ ]:
import os
import s3fs
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

BUCKET = "bdc2324-data"
fs.ls(BUCKET)

In [ ]:
# Chargement des fichiers campaign_stats.csv
FILE_PATH_S3 = 'bdc2324-data/1/1campaign_stats.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    campaign_stats_1 = pd.read_csv(file_in, sep=",")

FILE_PATH_S3 = 'bdc2324-data/2/2campaign_stats.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    campaign_stats_2 = pd.read_csv(file_in, sep=",")

FILE_PATH_S3 = 'bdc2324-data/3/3campaign_stats.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    campaign_stats_3 = pd.read_csv(file_in, sep=",")

In [ ]:
# Conversion des dates 'sent_at'
campaign_stats_1['sent_at'] = pd.to_datetime(campaign_stats_1['sent_at'], format = 'ISO8601', utc = True)
campaign_stats_2['sent_at'] = pd.to_datetime(campaign_stats_2['sent_at'], format = 'ISO8601', utc = True)
campaign_stats_3['sent_at'] = pd.to_datetime(campaign_stats_3['sent_at'], format = 'ISO8601', utc = True)

In [ ]:
# Chaque unites correspond à une période ? --> Non, les dossiers ont juste pour but de réduire la taille des fichiers
print(campaign_stats_1['sent_at'].max())
print(campaign_stats_1['sent_at'].min())

print(campaign_stats_2['sent_at'].max())
print(campaign_stats_2['sent_at'].min())

print(campaign_stats_3['sent_at'].max())
print(campaign_stats_3['sent_at'].min())

In [ ]:
campaign_stats_1['sent_at']

### Customersplus.csv

In [ ]:
FILE_PATH_S3 = 'bdc2324-data/1/1customersplus.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    customers_plus_1 = pd.read_csv(file_in, sep=",")

FILE_PATH_S3 = 'bdc2324-data/2/2customersplus.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    customers_plus_2 = pd.read_csv(file_in, sep=",")

In [ ]:
customers_plus_1.columns

In [ ]:
customers_plus_1.shape

In [ ]:
customers_plus_1['id'].nunique()

In [ ]:
customers_plus_2['id'].nunique()

In [ ]:
common_id = set(customers_plus_2['id']).intersection(customers_plus_1['id'])

In [ ]:
common_id = set(customers_plus_2['id']).intersection(customers_plus_1['id'])
# Exemple id commun = caractéristiques communes
print(customers_plus_2[customers_plus_2['id'] == list(common_id)[0]])

print(customers_plus_1[customers_plus_1['id'] == list(common_id)[0]])

In [ ]:
customers_plus_1.isna().mean()*100

In [ ]:
# Chargement de toutes les données
liste_base = ['customer_target_mappings', 'customersplus', 'target_types', 'tags', 'events', 'tickets', 'representations', 'purchases', 'products']

for nom_base in liste_base:
    FILE_PATH_S3 = 'bdc2324-data/11/11' + nom_base + '.csv'
    with fs.open(FILE_PATH_S3, mode="rb") as file_in:
        globals()[nom_base] = pd.read_csv(file_in, sep=",")

In [ ]:
# Jointure
merge_1 = pd.merge(purchases, tickets, left_on='id', right_on='purchase_id', how='inner')[['id_x', 'customer_id','product_id', 'purchase_date', 'type_of', 'is_from_subscription']]
merge_2 = pd.merge(products, merge_1, left_on='id', right_on='product_id', how='inner')[['id_x', 'customer_id', 'representation_id', 'purchase_date', 'type_of', 'is_from_subscription', 'amount', 'is_full_price']]
merge_3 = pd.merge(representations, merge_2, left_on='id', right_on='representation_id', how='inner')[['id_x', 'customer_id', 'event_id', 'purchase_date', 'type_of', 'is_from_subscription', 'amount', 'is_full_price', 'start_date_time']]
merge_4 = pd.merge(events, merge_3, left_on='id', right_on='event_id', how='inner')[['id_x', 'customer_id', 'purchase_date', 'type_of', 'is_from_subscription', 'amount', 'is_full_price', 'start_date_time', 'name']]
merge_4 = merge_4.rename(columns={'name': 'event_name'})
df_customer_event = pd.merge(customersplus, merge_4, left_on = 'id', right_on = 'customer_id', how = 'inner')[['id_x', 'purchase_date', 'type_of', 'is_from_subscription', 'amount', 'is_full_price', 'start_date_time', 'event_name']]
df_customer_event

# Fusion et exploration

In [ ]:
# Jointure
var_choosed = ['id_x', 'customer_id','product_id', 'purchase_date', 'type_of', 'is_from_subscription']
merge_1 = pd.merge(purchases, tickets, left_on='id', right_on='purchase_id', how='inner')[var_choosed]

var_choosed.extend(['amount', 'is_full_price', 'representation_id'])
merge_2 = pd.merge(products, merge_1, left_on='id', right_on='product_id', how='inner')[var_choosed]

var_choosed.remove('representation_id')
var_choosed.extend(['start_date_time', 'event_id'])
merge_3 = pd.merge(representations, merge_2, left_on='id', right_on='representation_id', how='inner')[var_choosed]

var_choosed.remove('event_id')
var_choosed.extend(['name', 'customer_id'])
merge_4 = pd.merge(events, merge_3, left_on='id', right_on='event_id', how='inner')[var_choosed]

# Changement de nom
merge_4 = merge_4.rename(columns={'name': 'event_name'})
var_choosed[var_choosed.index('name')] = "event_name"

# Base finale
var_choosed.extend(['age', 'gender', 'country', 'fidelity', 'profession'])
df_customer_event = pd.merge(customersplus, merge_4, left_on = 'id', right_on = 'customer_id', how = 'inner')[var_choosed]
df_customer_event

## Type de client au globale

In [ ]:
# Client
print(customer_target_mappings.columns)
print(customer_target_mappings.shape)
customer_target_mappings.info()

In [ ]:
customer_target_mappings['extra_field'].unique()

In [ ]:
customer_target_mappings['name'].unique()

In [ ]:
# Segmentation existante
print(target_types.columns)
print(target_types.shape)
target_types.info()

In [ ]:
target_types

In [ ]:
# Tags = clients
FILE_PATH_S3 = 'bdc2324-data/11/11tags.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    tags = pd.read_csv(file_in, sep=",")

print(tags.columns)
print(tags.shape)
tags.info()

In [ ]:
tags

In [ ]:
# Structure = clients
FILE_PATH_S3 = 'bdc2324-data/11/11structure_tag_mappings.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    structure_tag_mappings = pd.read_csv(file_in, sep=",")

print(structure_tag_mappings.columns)
print(structure_tag_mappings.shape)
structure_tag_mappings.info()

In [ ]:
structure_tag_mappings

In [ ]:
# Tags = clients
FILE_PATH_S3 = 'bdc2324-data/11/11customersplus.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    customersplus = pd.read_csv(file_in, sep=",")

print(customersplus.columns)
print(customersplus.shape)
customersplus.info()

In [ ]:
customersplus

In [ ]:
# But : lier les caractéristiques socio-demo et les comportements d'achat


In [ ]:
# tickets
FILE_PATH_S3 = 'bdc2324-data/11/11tickets.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    tickets = pd.read_csv(file_in, sep=",")

print(tickets.columns)
print(tickets.shape)
tickets.info()

In [ ]:
tickets

In [ ]:
tickets['type_of'].unique()

## Types d'évenement et client

In [ ]:
# Evenement = events.csv
FILE_PATH_S3 = 'bdc2324-data/11/11events.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    events = pd.read_csv(file_in, sep=",")

print(events.columns)
print(events.shape)
events.info()

In [ ]:
events

In [ ]:
events['name'].nunique()

In [ ]:
# Représentation des évenements = representations.csv
FILE_PATH_S3 = 'bdc2324-data/11/11representations.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    representations = pd.read_csv(file_in, sep=",")

print(representations.columns)
print(representations.shape)
representations.info()

In [ ]:
representations

In [ ]:
# Produits vendues = products.csv
FILE_PATH_S3 = 'bdc2324-data/11/11products.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    products = pd.read_csv(file_in, sep=",")

print(products.columns)
print(products.shape)
products.info()

In [ ]:
products

In [ ]:
# Lieu = facilities.csv
FILE_PATH_S3 = 'bdc2324-data/11/11facilities.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    facilities = pd.read_csv(file_in, sep=",")

print(facilities.columns)
print(facilities.shape)
facilities.info()

In [ ]:
facilities

In [ ]:
# Saisons = seasons.csv période sur deux années consécutives
FILE_PATH_S3 = 'bdc2324-data/11/11seasons.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    seasons = pd.read_csv(file_in, sep=",")

print(seasons.columns)
print(seasons.shape)
seasons.info()

In [ ]:
seasons['name'].unique()

In [ ]:
# Achats = purchases.csv 
FILE_PATH_S3 = 'bdc2324-data/11/11purchases.csv'

with fs.open(FILE_PATH_S3, mode="rb") as file_in:
    purchases = pd.read_csv(file_in, sep=",")

print(purchases.columns)
print(purchases.shape)
purchases.info()

In [ ]:
purchases